*Inspired by Sean Owen's [Blog](https://databricks.com/blog/2019/08/15/how-not-to-scale-deep-learning-in-6-easy-steps.html) and [Notebook](https://demo.cloud.databricks.com/#notebook/10675022), How (Not) to Scale Deep Learning in 6 Easy steps*

# Distributed Deep Learning on Databricks



Deep Learning continues to be an exciting and powerful tool for a large range of problems. It requires a large amount of compute, and often, users find that deep learning model training seems 'too slow'. Sometimes this is due to common, simple errors that can be avoided. But scaling deep learning also requires a different understanding of how to trade off speed, efficiency, and accuracy, and a new set of tools like Tensorflow, Petastorm, and Horovod.

This notebooks walks through training an image classifier on the flowers dataset starting with single node training and progressing to distributed training with GPU clusters.

## Data Preparation

This loads the [flowers dataset](https://databricks.com/notebooks/simple-aws/petastorm-spark-converter-tensorflow.html#:~:text=We%20use%20the-,flowers%20dataset,-from%20the%20TensorFlow) hosted by the Tensorflow team. It contains flower photos stored under five sub-directories, one per class. It is hosted under databricks-datasets `dbfs:/databricks-datasets/flower_photos` for easy access.

In this example, we load the flowers table which contains the preprocessed flowers dataset using binary file data source. We will use a small subset of the flowers dataset, including ~900 train images, and ~100 validation images.

In [0]:
import io, os
import numpy as np
import mlflow

from pyspark.sql.functions import col

In [0]:
bronze_df = spark.read.format("binaryFile").option("pathGlobFilter", "*.jpg").option("recursiveFileLookup", "true").load("/databricks-datasets/flower_photos/")
display(bronze_df)

path,modificationTime,length,content
dbfs:/databricks-datasets/flower_photos/tulips/2431737309_1468526f8b.jpg,2019-12-11T22:18:32.000+0000,281953,"List(/9j/4AAQSkZJRgABAQEBLAEsAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/sunflowers/4932735362_6e1017140f.jpg,2019-12-11T22:18:00.000+0000,277326,"List(/9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/tulips/8717900362_2aa508e9e5.jpg,2019-12-11T22:18:52.000+0000,265806,"List(/9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/sunflowers/4341530649_c17bbc5d01.jpg,2019-12-11T22:17:56.000+0000,257418,"List(/9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/daisy/5693459303_e61d9a9533.jpg,2019-12-11T22:16:30.000+0000,248540,"List(/9j/4AAQSkZJRgABAQEAYABgAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/tulips/5674170543_73e3f403fb.jpg,2019-12-11T22:18:42.000+0000,246285,"List(/9j/4AAQSkZJRgABAQEBLAEsAAD/4iH8SUNDX1BST0ZJTEUAAQEAACHsTktPTgIgAABtbnRyUkdCIFhZWiAH2QACABQAEQAHAAphY3NwQVBQTAAAAABub25lAAAAAQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLQAAAAAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/tulips/10164073235_f29931d91e.jpg,2019-12-11T22:18:17.000+0000,244431,"List(/9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/sunflowers/6140892289_92805cc590.jpg,2019-12-11T22:18:07.000+0000,243637,"List(/9j/4AAQSkZJRgABAQEASABIAAD/4iH8SUNDX1BST0ZJTEUAAQEAACHsTktPTgIgAABtbnRyUkdCIFhZWiAH2QACABQAEQAHAAphY3NwQVBQTAAAAABub25lAAAAAQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLQAAAAAAAAAAAAA= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/sunflowers/244074259_47ce6d3ef9.jpg,2019-12-11T22:17:50.000+0000,242637,"List(/9j/4AAQSkZJRgABAQEBLAEsAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)"
dbfs:/databricks-datasets/flower_photos/daisy/3704306975_75b74497d8.jpg,2019-12-11T22:16:24.000+0000,240957,"List(/9j/4AAQSkZJRgABAQEAYABgAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)"


In [0]:
# Load libraries
import shutil

# Set config for database name, file paths, and table names
database_name = 'distributed_dl_workshop'

# Move file from driver to DBFS
user = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')

# Paths for various Delta tables
bronze_tbl_path = '/home/{}/distributed_dl_workshop/bronze/'.format(user)
silver_tbl_path = '/home/{}/distributed_dl_workshop/silver/'.format(user)

bronze_tbl_name = 'bronze'
silver_tbl_name = 'silver'

# Delete the old database and tables if needed (for demo purposes)
_ = spark.sql('DROP DATABASE IF EXISTS {} CASCADE'.format(database_name))

# Create database to house tables
_ = spark.sql('CREATE DATABASE {}'.format(database_name))

# Drop any old delta lake files if needed (e.g. re-running this notebook with the same bronze_tbl_path and silver_tbl_path)
shutil.rmtree('/dbfs'+bronze_tbl_path, ignore_errors=True)
shutil.rmtree('/dbfs'+silver_tbl_path, ignore_errors=True)

### Creating Bronze Delta Table from Spark Dataframe

In [0]:
#To improve read performance when you load data back, Databricks recommends turning off compression when you save data loaded from binary files:
spark.conf.set("spark.sql.parquet.compression.codec", "uncompressed")

# Create a Delta Lake table from loaded 
bronze_df.write.format('delta').mode('overwrite').save(bronze_tbl_path)

In [0]:
# Create bronze table
_ = spark.sql('''
  CREATE TABLE `{}`.{}
  USING DELTA 
  LOCATION '{}'
  '''.format(database_name,bronze_tbl_name,bronze_tbl_path))

In [0]:
%sql
SELECT * FROM distributed_dl_workshop.bronze

path modificationTime length content dbfs:/databricks-datasets/flower_photos/daisy/100080576_f52e8ee070_n.jpg 2019-12-11T22:16:13.000+0000 26797 List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10140303196_b88d3d6cec.jpg 2019-12-11T22:16:13.000+0000 117247 List(/9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10172379554_b296050f82_n.jpg 2019-12-11T22:16:13.000+0000 36410 List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10172567486_2748826a8b.jpg 2019-12-11T22:16:13.000+0000 102862 List(/9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10172636503_21bededa75_n.jpg 2019-12-11T22:16:13.000+0000 27419 List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/102841525_bd6628ae3c.jpg 2019-12-11T22:16:13.000+0000 132803 List(/9j/4AAQSkZJRgABAQEBLAEsAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/1031799732_e7f4008c03.jpg 2019-12-11T22:16:13.000+0000 102618 List(/9j/4AAQSkZJRgABAQEASABIAAD/4gUoSUNDX1BST0ZJTEUAAQEAAAUYYXBwbAIgAABzY25yUkdCIFhZWiAH0wAHAAEAAAAAAABhY3NwQVBQTAAAAABhcHBsAAAAAAAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLWFwcGwAAAAAAAA= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10391248763_1d16681106_n.jpg 2019-12-11T22:16:13.000+0000 51688 List(/9j/4AAQSkZJRgABAQAAAQABAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10437754174_22ec990b77_m.jpg 2019-12-11T22:16:12.000+0000 13946 List(/9j/4AAQSkZJRgABAQAAAQABAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...) dbfs:/databricks-datasets/flower_photos/daisy/10437770546_8bb6f7bdd3_m.jpg 2019-12-11T22:16:13.000+0000 13518 List(/9j/4AAQSkZJRgABAQAAAQABAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), iVBORw0KGgoAAAANSUhEUgAAAGQAAABkCAIAAAD/gAIDAAArHUlEQVR42q3d99s1VZXm8QcBA+EFCb4qBlB0RLFtA4oK6Egr5oShwSwqKGKOGFFxQBhERQUUAyqYQ2srOuo4To/jGHEU/575PPXlWRTnxb7mslk/1FWnTp2qve59r7XXXjucrbvc5S5HHHHEPe5xj6OOOure9773f1rkmGOOuf/973/sscf+wyIPetCDHvzgBz/kIQ9x/MdFuujkoQ996HHHHXf88cc/+tGPPumkk04++eQnPOEJT3ziE5/61Kc+85nPfN7znvf85z//9NNPf8ELXvDCF77wpS996ctf/vIzzjjjla98pZMXv/jFz33uc5/2tKedcsopJy/yuMc97j/vyGMf+1gPPOGEEx75yEd6/sMe9rCH7oj3PvCBD3zAAx6gkPe73/3uu8jRRx99r3vd68gjj7znPe9Jnbvf/e70uutd77p79+7DDz/8Toscdthhhx56qOMd73jHgw8++KCDDtq1a9cBBxyw//7777fffk5c8ZV7/MrPPeSeixy5yJbH3e1ud/PZm7wPUl6vEIqiQCESUhU0yEKtiw9/+MPpQ6vHPOYxFKb5k5/8ZGA9+9nP/udFTjvtNGC96EUvgs6LFnnJS14CO1A+4xnPeNKTnvT4xz/+nxZZ4/XYRTxWNXi+txy3CNS8V8HUpUKq1/stAq/73Oc+6lutU2zAwoY7L0J/eAEuyA455BC4AOvAAw88YBHnEPSVe/wKLEAPpp55M7C8LFopxNAqUMjDFgmvuRKtHvWoR5144ok0pDblIYUvz3rWs9AKUjErpJyctshznvMcSD3lKU9BQ2R8/CKDV5ABy2Ph5RWPeMQjHr5IeKkteKlO5VS1xywCMuWnSLpFsYEs1CIavAJry

In [0]:
# load as a bronze table for faster transformations
bronze_df = spark.table("distributed_dl_workshop.bronze")

Reading from a Delta table is much faster than trying to load all the images from a directory! By saving the data in the Delta format, we can continue to process the images into a silver table, transforming it into a proper training set for our use case. This entails parsing out labels from the image paths and converting string labels into numerical values.

### Create Silver Table from Bronze Table

In [0]:
#custom udf to extract labels out of image paths
from pyspark.sql.functions import udf
from pyspark.ml.feature import StringIndexer

# convert string categories to numerical 
indexer = StringIndexer(inputCol="category", outputCol="label")


@udf("string")
def extract_category(path):
  return path.split("/")[-2]

df = bronze_df.withColumn("category", extract_category("path"))
silver_df = indexer.fit(df).transform(df)
display(silver_df)

path,modificationTime,length,content,category,label
dbfs:/databricks-datasets/flower_photos/sunflowers/4895720722_8247f2015b_n.jpg,2019-12-11T22:17:59.000+0000,38988,"List(/9j/4AAQSkZJRgABAQAAAQABAAD/7QDIUGhvdG9zaG9wIDMuMAA4QklNBAQAAAAAAKscAhkABEJhcm4cAhkAA0NCRhwCGQAZQ2hlc2FwZWFrZSBCYXkgRm91bmRhdGlvbhwCGQAMQ2xhZ2V0dCBGYXJtHAIZAB9Db21tdW5pdHk= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4895721242_89014e723c_n.jpg,2019-12-11T22:17:59.000+0000,48806,"List(/9j/4AAQSkZJRgABAQAAAQABAAD/7QC+UGhvdG9zaG9wIDMuMAA4QklNBAQAAAAAAKIcAhkAA0NCRhwCGQAZQ2hlc2FwZWFrZSBCYXkgRm91bmRhdGlvbhwCGQAMQ2xhZ2V0dCBGYXJtHAIZAB9Db21tdW5pdHkgU3VwcG9ydGU= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4895721788_f10208ab77_n.jpg,2019-12-11T22:17:59.000+0000,47944,"List(/9j/4AAQSkZJRgABAQAAAQABAAD/7QC+UGhvdG9zaG9wIDMuMAA4QklNBAQAAAAAAKIcAhkAA0NCRhwCGQAZQ2hlc2FwZWFrZSBCYXkgRm91bmRhdGlvbhwCGQAMQ2xhZ2V0dCBGYXJtHAIZAB9Db21tdW5pdHkgU3VwcG9ydGU= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4914793782_d0ea760791.jpg,2019-12-11T22:17:59.000+0000,196820,"List(/9j/4AAQSkZJRgABAQEA8ADwAAD/4gJASUNDX1BST0ZJTEUAAQEAAAIwQURCRQIQAABtbnRyUkdCIFhZWiAHzwAGAAMAAAAAAABhY3NwQVBQTAAAAABub25lAAAAAAAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUFEQkUAAAAAAAA= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4927658421_7eed83bc95_m.jpg,2019-12-11T22:17:59.000+0000,25802,"List(/9j/4AAQSkZJRgABAQAAAQABAAD//gAMQXBwbGVNYXJrCv/iBShJQ0NfUFJPRklMRQABAQAABRhhcHBsAiAAAHNjbnJSR0IgWFlaIAfTAAcAAQAAAAAAAGFjc3BBUFBMAAAAAGFwcGwAAAAAAAAAAAAAAAAAAAAAAAD21gABAAA= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4932143849_018486cbf7.jpg,2019-12-11T22:17:59.000+0000,219559,"List(/9j/4AAQSkZJRgABAQEBXgFeAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4932144003_cbffc89bf0.jpg,2019-12-11T22:17:59.000+0000,177082,"List(/9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4932735362_6e1017140f.jpg,2019-12-11T22:18:00.000+0000,277326,"List(/9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4932735566_2327bf319a.jpg,2019-12-11T22:18:00.000+0000,185905,"List(/9j/4AAQSkZJRgABAQEBXgFeAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)",sunflowers,2.0
dbfs:/databricks-datasets/flower_photos/sunflowers/4932736136_0115955987.jpg,2019-12-11T22:18:00.000+0000,153253,"List(/9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated), ...)",sunflowers,2.0


In [0]:
# save as delta table
silver_df.write.format('delta').mode('overwrite').save(silver_tbl_path)

# Create silver table
_ = spark.sql('''
  CREATE TABLE `{}`.{}
  USING DELTA 
  LOCATION '{}'
  '''.format(database_name,silver_tbl_name,silver_tbl_path))

Having transformed and saved our data into a silver table, we can select the columns we'll need for training.

In [0]:
dataset_df = spark.table("distributed_dl_workshop.silver").select("content", "label")
display(dataset_df)

content,label
"List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQEASABIAAD//gAMQXBwbGVNYXJrCv/iBShJQ0NfUFJPRklMRQABAQAABRhhcHBsAiAAAHNjbnJSR0IgWFlaIAfTAAcAAQAAAAAAAGFjc3BBUFBMAAAAAGFwcGwAAAAAAAAAAAAAAAAAAAAAAAD21gABAAA= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQAAAQABAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQEASABIAAD//gAMQXBwbGVNYXJrCv/iBShJQ0NfUFJPRklMRQABAQAABRhhcHBsAiAAAHNjbnJSR0IgWFlaIAfTAAcAAQAAAAAAAGFjc3BBUFBMAAAAAGFwcGwAAAAAAAAAAAAAAAAAAAAAAAD21gABAAA= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQEA8ADwAAD/4gJASUNDX1BST0ZJTEUAAQEAAAIwQURCRQIQAABtbnRyUkdCIFhZWiAHzwAGAAMAAAAAAABhY3NwQVBQTAAAAABub25lAAAAAAAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUFEQkUAAAAAAAA= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAMCAgMCAgMDAwMEAwMEBQgFBQQEBQoHBwYIDAoMDAsKCwsNDhIQDQ4RDgsLEBYQERMUFRUVDA8XGBYUGBIUFRT/2wBDAQMEBAUEBQkFBQkUDQsNFBQUFBQUFBQUFBQUFBQUFBQUFBQ= (truncated), ...)",0.0
"List(/9j/4AAQSkZJRgABAQEBXgFeAAD/4gxUSUNDX1BST0ZJTEUAAQEAAAxEVUNDTQJAAABtbnRyUkdCIFhZWiAH0wAEAAQAAAAAAABhY3NwTVNGVAAAAABDQU5PWjAwOQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUNBTk8AAAAAAAA= (truncated), ...)",0.0


Let's get the number of possible labels we'll need to classify. For testing purposes, we'll use a subset of the data and split it into a `train` and `val` dataset.

In [0]:
img_size = 224
num_classes = dataset_df.select("label").distinct().count()
df_train, df_val = dataset_df.randomSplit([0.9, 0.1], seed=12345)

Let's save our `train` and `val` datasets into delta lake tables for future use.

In [0]:
#split our silver table into proper train and val tables

silver_train_tbl_path = '/home/{}/distributed_dl_workshop/silver_train/'.format(user)
silver_val_tbl_path = '/home/{}/distributed_dl_workshop/silver_val/'.format(user)

silver_train_tbl_name = 'silver_train'
silver_val_tbl_name = 'silver_val'


# Drop any old delta lake files if needed (e.g. re-running this notebook with the same paths)
shutil.rmtree('/dbfs'+silver_train_tbl_path, ignore_errors=True)
shutil.rmtree('/dbfs'+silver_val_tbl_path, ignore_errors=True)

# save as delta table
df_train.write.format('delta').mode('overwrite').save(silver_train_tbl_path)
df_val.write.format('delta').mode('overwrite').save(silver_val_tbl_path)

# Create silver table
_ = spark.sql('''
  CREATE TABLE `{}`.{}
  USING DELTA 
  LOCATION '{}'
  '''.format(database_name,silver_train_tbl_name,silver_train_tbl_path))

_ = spark.sql('''
  CREATE TABLE `{}`.{}
  USING DELTA 
  LOCATION '{}'
  '''.format(database_name,silver_val_tbl_name,silver_val_tbl_path))

To train a model with Tensorflow, we'll need to transform our spark dataframes into `tf.data.Dataset`s. Tensorflow has a function to transform a pandas dataframe into a [tensorflow dataset](https://www.tensorflow.org/datasets).
For this example, we'll convert our dataframe to a pandas dataframe using `.toPandas()` and convert to a properly formated tf dataset from there.

In [0]:
import tensorflow as tf

features = ["content" "label"]

pd_train = df_train.toPandas() 
pd_val = df_val.toPandas()

train_dataset = (
    tf.data.Dataset.from_tensor_slices(
        (pd_train["content"].values,pd_train["label"].values))
)

val_dataset = (
    tf.data.Dataset.from_tensor_slices(
        (pd_val["content"].values,pd_val["label"].values))
)

Now we can continue transforming our image dataset into the correct format using a preprocessing function and mapping it to our `tf.datasets`

In [0]:
from tensorflow.keras.applications.mobilenet_v2 import preprocess_input

batch_size = 32

def preprocess(content, label):
  """
  Preprocess an image file bytes for MobileNetV2 (ImageNet).
  """
  image = tf.image.decode_jpeg(content, channels=3)
  image = tf.image.resize(image, [img_size,img_size])
  return preprocess_input(image), label

train_dataset = train_dataset.map(lambda content, label: preprocess(content, label)).batch(batch_size)
val_dataset = val_dataset.map(lambda content, label: preprocess(content, label)).batch(batch_size)

## Single Node Training

Single node training is the most common way machine learning practitioners set up their training regimes. For some modeling use cases, this is a great way to go as all the modeling can stay on one machine with no additional libraries. 

Training with Databricks is just as easy. Simply use a [Single Node Cluster](https://docs.databricks.com/clusters/single-node.html) which is just a Spark Driver with no worker nodes.

In [0]:
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam

# Additional options here will be used later:

def build_model():
  base_model = tf.keras.applications.MobileNetV2(include_top=False, input_shape=(img_size, img_size, 3))
  
  #freeze base model layers
  for layer in base_model.layers:
    layer.trainable = False
    
  model = Sequential([
    base_model, 
    tf.keras.layers.GlobalAveragePooling2D(),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(num_classes, activation="softmax")
  ])

  return model

In [0]:
# mlflow autologging
mlflow.tensorflow.autolog()

model = build_model()
model.compile(optimizer=Adam(learning_rate=0.001), loss='sparse_categorical_crossentropy', metrics=['accuracy'])

epochs = 3
steps_per_epoch = len(train_dataset) // batch_size
validation_steps = len(val_dataset) // batch_size

model.fit(train_dataset,
                   steps_per_epoch = steps_per_epoch,
                   epochs = epochs,
                   verbose = 1,
                   validation_data = val_dataset,
                   validation_steps = validation_steps)

Downloading data from https://storage.googleapis.com/tensorflow/keras-applications/mobilenet_v2/mobilenet_v2_weights_tf_dim_ordering_tf_kernels_1.0_224_no_top.h5
 16384/9406464 [..............................] - ETA: 1s 229376/9406464 [..............................] - ETA: 2s3596288/9406464 [==========>...................] - ETA: 0s9412608/9406464 [==============================] - 0s 0us/step
9420800/9406464 [==============================] - 0s 0us/step
2021/12/07 05:18:43 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID '00d92800f00344999e834b45847b8dc3', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current tensorflow workflow
/databricks/python/lib/python3.8/site-packages/keras/utils/generic_utils.py:494: CustomMaskWarning: Custom mask layers require a config and must override get_config. When loading, the custom mask layer must be passed to the custom_objects argument.
 warnings.warn('Custom mask layers require a config and must override '
Epoch 1/3
1/3 [=========>....................] - ETA: 15s - loss: 2.3583 - accuracy: 0.15622/3 [===================>..........] - ETA: 0s - loss: 1.9133 - accuracy: 0.2500 3/3 [==============================] - ETA: 0s - loss: 1.7678 - accuracy: 0.29173/3 [==============================] - 9s 475ms/step - loss: 1.7678 - accuracy: 0.2917
Epoch 2/3
1/3 [=========>....................] - ETA: 0s - loss: 1.1086 - accuracy: 0.59383/3 [==============================] - ETA: 0s - loss: 0.6982 - accuracy: 0.78123/3 [==============================] - 0s 43ms/step - loss: 0.6982 - accuracy: 0.7812
Epoch 3/3
1/3 [=========>....................] - ETA: 0s - loss: 0.2213 - accuracy: 0.9375WARNING:tensorflow:Callback method `on_train_batch_begin` is slow compared to the batch time (batch time: 0.0363s vs `on_train_batch_begin` time: 0.0822s). Check your callbacks.
3/3 [==============================] - ETA: 0s - loss: 0.1020 - accuracy: 0.97923/3 [==============================] - 0s 44ms/step - loss: 0.1020 - accuracy: 0.9792
WARNING:absl:Function `_wrapped_model` contains input name(s) mobilenetv2_1.00_224_input with unsupported characters which will be renamed to mobilenetv2_1_00_224_input in the SavedModel.
INFO:tensorflow:Assets written to: /tmp/tmp6vzxgy0f/model/data/model/assets
INFO:tensorflow:Assets written to: /tmp/tmp6vzxgy0f/model/data/model/assets
/databricks/python/lib/python3.8/site-packages/keras/utils/generic_utils.py:494: CustomMaskWarning: Custom mask layers require a config and must override get_config. When loading, the custom mask layer must be passed to the custom_objects argument.
 warnings.warn('Custom mask layers require a config and must override '
Out[15]: <keras.callbacks.History at 0x7f78b1af02b0>

Wohoo! We trained a model on a single machine very similarly to what you might have done on your laptop. It was easy for us to convert this small dataset into a pandas dataframe from a delta table and ultimately convert it into a tensorflow dataset for training. 

However, most production workloads will require training with **orders of magnitude** more data, so much so that it could overwhelm a single machine while training. Other cases could contribute to exhausting a single node during training such as training large model architectures.

## Distributed Training

A very large training problem may benefit from scaling out verticaly (training on a larger instance) or horizontally (using multiple machines). Scaling vertically may be an approach to adopt, but it can be costly to run a large instance for an extended period of time and scaling a single machine is limited (ie. there's only so many cores + RAM one machine could have). 

Scaling horizontally can be an affordable way to leverage the compute required to tackle very large training events. Multiple smaller instances may be more readibily available at cheaper rates in the cloud than a single, very large instance. Theoretically, you could add as many nodes as you wish (dependent on your cloud limits). In this section, we'll go over how to incorporate [Petastorm](https://docs.databricks.com/applications/machine-learning/load-data/ddl-data.html) and [Horovod](https://docs.databricks.com/applications/machine-learning/train-model/distributed-training/horovod-runner.html) into our single node training regime to distribute training to multiple machines.

### 1. Loading data with Petastorm

Our first single node training example only used a fraction of the data and it required to work with the data sitting in memory. Typical datasets used for training may not fit in memory for a single machine. Petastorm enables directly loading data stored in parquet format, meaning we can go from our silver Delta table to a distributed `tf.data.Dataset` without having to copy our table into a `Pandas` dataframe and wasting additional memory.

First, let's split our silver table into train and val tables:

Here we use `petastorm` to load and cache data that was read directly from our silver train and val Delta tables:

In [0]:
df_train = spark.read.format("delta").load(silver_train_tbl_path)
df_val = spark.read.format("delta").load(silver_val_tbl_path)

# Make sure the number of partitions is at least the number of workers which is required for distributed training.
df_train = df_train.repartition(2)
df_val = df_val.repartition(2)

In [0]:
from petastorm.spark import SparkDatasetConverter, make_spark_converter

dbutils.fs.rm("/tmp/distributed_dl_workshop/petastorm", recurse=True)
spark.conf.set(SparkDatasetConverter.PARENT_CACHE_DIR_URL_CONF, "file:///dbfs/tmp/distributed_dl_workshop/petastorm")

converter_train = make_spark_converter(df_train)
converter_val = make_spark_converter(df_val)

train_size = len(converter_train)
val_size = len(converter_val)

/databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py:158: FutureWarning: pyarrow.LocalFileSystem is deprecated as of 2.0.0, please use pyarrow.fs.LocalFileSystem instead.
 original_result = python_builtin_import(name, globals, locals, fromlist, level)
/databricks/python/lib/python3.8/site-packages/petastorm/spark/spark_dataset_converter.py:28: FutureWarning: pyarrow.LocalFileSystem is deprecated as of 2.0.0, please use pyarrow.fs.LocalFileSystem instead.
 from pyarrow import LocalFileSystem
/databricks/python/lib/python3.8/site-packages/petastorm/fs_utils.py:88: FutureWarning: pyarrow.localfs is deprecated as of 2.0.0, please use pyarrow.fs.LocalFileSystem instead.
 self._filesystem = pyarrow.localfs
WARNING:petastorm.spark.spark_dataset_converter:Converting floating-point columns to float32
WARNING:petastorm.spark.spark_dataset_converter:Converting floating-point columns to float32
WARNING:petastorm.spark.spark_dataset_converter:The median size 12578325 B (< 50 MB) of the parquet files is too small. Total size: 23942805 B. Increase the median file size by calling df.repartition(n) or df.coalesce(n), which might help improve the performance. Parquet files: file:/dbfs/tmp/distributed_dl_workshop/petastorm/20211207051942-appid-app-20211207050924-0000-a2a18f6c-21ec-437b-9ac2-7141e91dbed9/part-00000-tid-7294532247391893353-9cf7be5e-ffb0-4cac-a97e-b25b2b29c3b3-259-1-c000.parquet, ...

In [0]:
with converter_train.make_tf_dataset(batch_size=batch_size) as train_ds,\
     converter_val.make_tf_dataset(batch_size=batch_size) as val_ds:
  
  # mlflow autologging
  mlflow.tensorflow.autolog()
  
  # Transforming datasets to map our preprocess function() and then batch()
  train_ds = train_ds.unbatch().map(lambda x: (x.content, x.label))
  val_ds = val_ds.unbatch().map(lambda x: (x.content, x.label))
  
  train_ds = train_ds.map(lambda content, label: preprocess(content, label)).batch(batch_size)
  val_ds = val_ds.map(lambda content, label: preprocess(content, label)).batch(batch_size)
  
  model = build_model()
  model.compile(optimizer=Adam(learning_rate=0.001), loss='sparse_categorical_crossentropy', metrics=['accuracy'])

  epochs = 3
  steps_per_epoch = train_size // batch_size
  validation_steps = val_size // batch_size

  model.fit(train_ds,
            steps_per_epoch = steps_per_epoch,
            epochs = epochs,
            verbose = 1,
            validation_data = val_ds,
            validation_steps = validation_steps)

2021/12/07 05:19:50 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID 'dceefff3e5dc49d2bf1af0f222008c21', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current tensorflow workflow
Epoch 1/3
 1/103 [..............................] - ETA: 4:21 - loss: 3.4311 - accuracy: 0.0000e+00 2/103 [..............................] - ETA: 1:15 - loss: 3.0589 - accuracy: 0.0625  3/103 [..............................] - ETA: 51s - loss: 2.9171 - accuracy: 0.0833  4/103 [>.............................] - ETA: 35s - loss: 2.7843 - accuracy: 0.0859 5/103 [>.............................] - ETA: 27s - loss: 2.8656 - accuracy: 0.0750 6/103 [>.............................] - ETA: 22s - loss: 2.8878 - accuracy: 0.0781WARNING:tensorflow:Callback method `on_train_batch_begin` is slow compared to the batch time (batch time: 0.0518s vs `on_train_batch_begin` time: 0.1010s). Check your callbacks.
WARNING:tensorflow:Callback method `on_train_batch_begin` is slow compared to the batch time (batch time: 0.0518s vs `on_train_batch_begin` time: 0.1010s). Check your callbacks.
WARNING:tensorflow:Callback method `on_train_batch_end` is slow compared to the batch time (batch time: 0.0518s vs `on_train_batch_end` time: 0.0534s). Check your callbacks.
WARNING:tensorflow:Callback method `on_train_batch_end` is slow compared to the batch time (batch time: 0.0518s vs `on_train_batch_end` time: 0.0534s). Check your callbacks.
 8/103 [=>............................] - ETA: 17s - loss: 3.0645 - accuracy: 0.0938 10/103 [=>............................] - ETA: 13s - loss: 3.2036 - accuracy: 0.1000 12/103 [==>...........................] - ETA: 11s - loss: 3.2001 - accuracy: 0.0938 14/103 [===>..........................] - ETA: 10s - loss: 3.0324 - accuracy: 0.1183 16/103 [===>..........................] - ETA: 9s - loss: 2.8764 - accuracy: 0.1426  18/103 [====>.........................] - ETA: 8s - loss: 2.7094 - accuracy: 0.1719 20/103 [====>.........................] - ETA: 7s - loss: 2.5536 - accuracy: 0.2016 22/103 [=====>........................] - ETA: 6s - loss: 2.4274 - accuracy: 0.2344 24/103 [=====>........................] - ETA: 6s - loss: 2.4896 - accuracy: 0.2305 26/103 [======>.......................] - ETA: 6s - loss: 2.5727 - accuracy: 0.2188 28/103 [=======>......................] - ETA: 5s - loss: 2.5989 - accuracy: 0.2109 30/103 [=======>......................] - ETA: 5s - loss: 2.6671 - accuracy: 0.2062

You can see the code to train our model is exactly the same as our single node training. Adding Petastorm to load our data directly from the underlying parquet files in our delta tables simply required using the `make_spark_converter` class and initializing our datasets using the `make_tf_dataset()` method.

Next, we need to distribute the training across our cluster.

### 2. Distribute training with Horovod

[Horovod](https://github.com/horovod/horovod) is a distributed training framework for TensorFlow, Keras, and PyTorch. Databricks supports distributed deep learning training using HorovodRunner and the `horovod.spark` package which we will use next. 

We can use Horovod to train across multiple machines, meaning we can distribute training across CPU-clusters or GPU clusters.

[HorovodRunner](https://docs.databricks.com/applications/machine-learning/train-model/distributed-training/horovod-runner.html#:~:text=HorovodRunner%20is%20a%20general%20API,learning%20training%20jobs%20on%20Spark.) takes a Python method that contains deep learning training code with Horovod hooks. HorovodRunner pickles the method on the driver and distributes it to Spark workers. Essentially, this API lets you launch Horovod training jobs as Spark jobs! To be able to work with HorovodRunner correcty, we need to package all of our logic into a function. This will ensure the logic is distributed across each node.

Inside our function, we'll incorporate the same logic we used in the single node and petastorm training examples plus additional logic to account for GPUs. 

If you have a CPU cluster, then these lines will be ignored and training will occur on CPU.

In [0]:
import horovod.tensorflow.keras as hvd
from sparkdl import HorovodRunner

databricks_host = 'https://field-eng.cloud.databricks.com/'
databricks_token = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiToken().get()

def train_and_evaluate_hvd():
  hvd.init()  # Initialize Horovod.
  
  mlflow.mlflow.set_tracking_uri('databricks')
  os.environ['DATABRICKS_HOST'] = databricks_host
  os.environ['DATABRICKS_TOKEN'] = databricks_token
  
  # Horovod: pin GPU to be used to process local rank (one GPU per process)
  gpus = tf.config.experimental.list_physical_devices('GPU')
  for gpu in gpus:
    tf.config.experimental.set_memory_growth(gpu, True)
  if gpus:
    tf.config.experimental.set_visible_devices(gpus[hvd.local_rank()], 'GPU')
      
  # Creating model
  model = build_model()
  
  # Horovod: adjust learning rate based on number of workers.
  optimizer = tf.keras.optimizers.Adam(learning_rate=0.001 * hvd.size())
  dist_optimizer = hvd.DistributedOptimizer(optimizer)
  
  callbacks = [
    # Horovod: broadcast initial variable states from rank 0 to all other processes.
    # This is necessary to ensure consistent initialization of all workers when
    # training is started with random weights or restored from a checkpoint.
    hvd.callbacks.BroadcastGlobalVariablesCallback(0),
    hvd.callbacks.MetricAverageCallback(),
  ]
  
  # Set experimental_run_tf_function=False in TF 2.x
  model.compile(optimizer=dist_optimizer, 
                loss="sparse_categorical_crossentropy", 
                metrics=["accuracy"],
                experimental_run_tf_function=False)
  
    
  # same logic as Petastorm training example here with slight adjustments
  with converter_train.make_tf_dataset(batch_size=batch_size, cur_shard=hvd.rank(), shard_count=hvd.size()) as train_ds,\
     converter_val.make_tf_dataset(batch_size=batch_size, cur_shard=hvd.rank(), shard_count=hvd.size()) as val_ds:
    
    # Transforming datasets to map our preprocess function() and then batch()
    train_ds = train_ds.unbatch().map(lambda x: (x.content, x.label))
    val_ds = val_ds.unbatch().map(lambda x: (x.content, x.label))
  
    train_ds = train_ds.map(lambda content, label: preprocess(content, label)).batch(batch_size)
    val_ds = val_ds.map(lambda content, label: preprocess(content, label)).batch(batch_size)

    epochs = 3
    steps_per_epoch = train_size // (batch_size * hvd.size())
    validation_steps = max(1, val_size // (batch_size * hvd.size()))

    hist = model.fit(train_ds,
              steps_per_epoch = steps_per_epoch,
              epochs = epochs,
              verbose = 1,
              validation_data = val_ds,
              validation_steps = validation_steps)
    # MLflow Tracking (Log only from Worker 0)
    if hvd.rank() == 0:
      # Log events to MLflow
      with mlflow.start_run(run_id = active_run_uuid):
        # Log MLflow Parameters
        mlflow.log_param("epochs", epochs)
        mlflow.log_param("batch_size", batch_size)
        
        # Log MLflow Metrics
        mlflow.log_metric("val Loss", hist.history['val_loss'][-1])
        mlflow.log_metric("val Accuracy", hist.history['val_accuracy'][-1])
      
        # Log Model
        mlflow.keras.log_model(model, "models")
  
  return hist.history['val_loss'][-1], hist.history['val_accuracy'][-1]

In [0]:
with mlflow.start_run() as run:
  active_run_uuid = mlflow.active_run().info.run_uuid
  hr = HorovodRunner(np=2, driver_log_verbosity='all')  # This assumes the cluster consists of two workers.
  hr.run(train_and_evaluate_hvd)
mlflow.end_run()

INFO:HorovodRunner:The global names read or written to by the pickled function are {'val_size', 'converter_val', 'databricks_token', 'hvd', 'train_size', 'mlflow', 'tf', 'batch_size', 'build_model', 'active_run_uuid', 'converter_train', 'os', 'preprocess', 'databricks_host', 'max'}.
INFO:HorovodRunner:The pickled object size is 6128 bytes.
INFO:HorovodRunner:
### How to enable Horovod Timeline? ###
HorovodRunner has the ability to record the timeline of its activity with Horovod Timeline. To
record a Horovod Timeline, set the `HOROVOD_TIMELINE` environment variable to the location of the
timeline file to be created. You can then open the timeline file using the chrome://tracing
facility of the Chrome browser.

/databricks/spark/python/pyspark/sql/context.py:82: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
 warnings.warn(
INFO:HorovodRunner:Start training.
Warning: Permanently added '10.126.252.91' (ECDSA) to the list of known hosts.
[1,0]<stderr>:/databricks/python/lib/python3.8/site-packages/petastorm/spark/spark_dataset_converter.py:28: FutureWarning: pyarrow.LocalFileSystem is deprecated as of 2.0.0, please use pyarrow.fs.LocalFileSystem instead.
[1,0]<stderr>: from pyarrow import LocalFileSystem
[1,1]<stderr>:2021-12-07 05:20:59.698332: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,0]<stderr>:2021-12-07 05:20:59.698576: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,0]<stderr>:2021-12-07 05:20:59.708322: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,1]<stderr>:2021-12-07 05:20:59.708418: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,0]<stderr>:2021-12-07 05:20:59.709330: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,1]<stderr>:2021-12-07 05:20:59.709422: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,0]<stderr>:2021-12-07 05:20:59.720782: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations: AVX2 AVX512F FMA
[1,0]<stderr>:To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
[1,1]<stderr>:2021-12-07 05:20:59.721024: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations: AVX2 AVX512F FMA
[1,1]<stderr>:To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
[1,0]<stderr>:2021-12-07 05:20:59.721263: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,1]<stderr>:2021-12-07 05:20:59.721456: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
[1,0]<stderr>:2021-12-07 05:20:59.722240: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUM

## Monitoring and Optimizing

### Single node vs Distributed Training Cosiderations

Whether you choose to train in a distributed manner or using a single VM will be highly dependent on the scale of your training data and architecture complexity + size. There may be instances where leveraging Petastorm will help get past memory issues around dataset loading but distributing training across a cluster may add too much additional training time and/or underutilized resources.

Petastorm is very useful in situations were training data is the bottleneck. Distributing the dataset across the cluster is a great way to get past the memory limitations of a single node.

Horovod allows us to leverage the compute of multiple machines OR multiple devices (like GPUs) during training. This trait is especially useful when training with large architectures and/or massive datasets. At times leveraging multiple machines with a single GPU could be more cost effective than using a single, very large machine with multiple GPUs.

Given all of these options, how do you best tune the resources you'll need for your training needs?

### Ganglia Metrics

Found under the **Metrics** tab, [Ganglia](https://docs.databricks.com/clusters/clusters-manage.html#monitor-performance) live metrics and historical snapshots provide a view into how cluster resources are utilized at any point in time. 

![ganglia metrics](https://docs.databricks.com/_images/metrics-tab.png)

### Optimizations

Understanding how to interpret Ganglia metrics, you can observe these as you experiment with techniques that can further optimize your training.

#### Early Stopping

Early stopping can prevent you from potentially overfitting and/or waste compute resources by monitoring a metric of interest. In this example we may measure `val_accuracy`, to end training early when the metric no longer shows improvement. You can dial the sensitivity of this setting by adjusting the `patience` parameter.

Add this as part of your `callbacks` parameter in the `fit()` method.

```python

# add Early Stopping as a list for the callbacks parameter
callbacks = [
  tf.keras.callbacks.EarlyStopping(
    monitor="val_loss",
    patience=3 # Number of epochs with no improvement after which training will be stopped
  )
]

# ...

hist = model.fit(train_ds,
              steps_per_epoch = steps_per_epoch,
              epochs = epochs,
              verbose = 1,
              validation_data = val_ds,
              validation_steps = validation_steps,
              callbacks=callbacks)
```

#### Larger Batch sizes

You can improve training speed and potentially [boost model performance](https://arxiv.org/abs/2012.08795) by increasing the batch size during training. Larger batch sizes can help stabilize training but may take more resources (memory + compute) to load and process. If you find you are underwhelming your cluster resources, this could be a good knob to turn to increase utilization and speed up training.

#### Adapt Learning Rate

A larger learning rate may also help the model converge to a local minima faster by allowing the model weights to change more dramatically between epochs. Although it *may* find a local minima faster, this could lead to a suboptimal solution or even derail training all together where the model may not be able to converge. 

This parameter is a powerful one to experiment with and machine learning practitioners should be encouraged to do so! One can tune this by trial and error or by implementing a scheduler that can vary the parameter depending on duration of training or in response to some observed training progress.

More on the learning rate parameter can be found in this [reference](https://amzn.to/2NJW3gE).